# Cleaning Names

The purpose of this notebook is to clean the names of individuals. All the problems that we aim to fix in this notebook are listed [here](https://docs.google.com/document/d/1pcSQfWNll6K9tl-_rB4lztN0TsZsclU9vOnbyQob-Zs/edit).

In [3]:
# import all the necessary packages
import pandas as pd 
import numpy as np
import re
import csv
import ast

In [245]:
# import aggregated debt file
agg_debt = pd.read_csv('data/final_agg_debt.csv')

/var/folders/yl/q3pyym191yb9gkpy29l174z9tfwfvv/T/ipykernel_70749/4157892421.py:2: DtypeWarning: Columns (1,7,9,10,12,14,15,16,19,20,21,24,31) have mixed types. Specify dtype option on import or set low_memory=False.
  agg_debt = pd.read_csv('data/final_agg_debt.csv')


In [246]:
print(agg_debt.dtypes)

Unnamed: 0                                 int64
letter                                    object
date of the certificate | month          float64
date of the certificate | day            float64
date of the certificate | year           float64
to whom due | first name                  object
to whom due | last name                   object
to whom due | title                       object
time when the debt became due | month    float64
time when the debt became due | day       object
time when the debt became due | year      object
amount | dollars                         float64
amount | 90th                             object
line strike through? | yes?              float64
line strike through? | note               object
notes                                     object
state                                     object
org_file                                  object
org_index                                  int64
to whom due | title.1                     object
to whom due | first 

## Documenting Changes

<b>Goal: </b> We need to document changes we make to ```agg_debt.csv``` in a separate dataframe: ```name_changes```. This way, we can double-check whether those changes were appropriate. 

<b>Steps</b>
1. Create an empty dataframe. Here are the column names:
    - ```title_org```: The original title of the individual (Mr., Ms., etc.)
    - ```title_new```: The new title of the individual (Mr., Ms., etc.) 
    - ```first_name_org```: The original first name of the individual from the unchanged ```agg_debt.csv```
    - ```last_name_org```: The original last name of the individual from the unchanged ```agg_debt.csv``` 
    - ```first_name_new``` : If first name changed, record it here. Otherwise, this entry will still be the old name. 
    - ```last_name_new```: If last name changed, record it here. Otherwise, this entry will still be the old name. 
    - ```cleaning case```: This corresponds with the task number in the objectives document linked above. 
    - ```file_loc```: The individual state filename in which the row came from 
    - ```org_index```: The original index/row that the debt entry can be found in ```file_loc``` 
2. Create a function that adds a new row to the dataframe. This function will be called while we are cleaning. 

**Cleaning case = Objective number** 
- Clean company names = 2,
- Handle two names = 3,
- Handle abbreviations = 5,
- Standardize names (Ancestry) = 6

In [247]:
# record changes in this dataframe
name_changes = pd.DataFrame({'title_org': pd.Series(dtype='str'),
                       'title_new': pd.Series(dtype='str'),
                       'first_name_org': pd.Series(dtype='str'),
                       'last_name_org': pd.Series(dtype='str'),
                       'first_name_new': pd.Series(dtype='str'),
                       'last_name_new': pd.Series(dtype='str'),
                       'cleaning case': pd.Series(dtype='int'),
                       'file_loc': pd.Series(dtype='str'),
                       'org_index': pd.Series(dtype='int')})

In [248]:
def add_changes(title_org, title_new, fn_org, ln_org, fn_new, ln_new, case, file, index):
    name_changes.loc[len(name_changes.index)] = [title_org, title_new, fn_org, ln_org, fn_new, ln_new, case, file, index]

## Company Names

<b>Goal: </b> Some debt entries are actually company names or represent a group of people (example: ```James Vernon & Co.```). 

<b>Steps: </b>
1. Use string parsing to find if a debt entry has '& co' or '& others' in it's name. Note: I noticed these company names appear in the first name column. I do <b>not</b> run this program on the last name column.
2. I remove the '& co' or '& others' from the name. I use a human name parser library. This library can find out what parts of the name are the first name versus last name. 
3. I put the first name and last name in their own respective columns. 
4. Record name change in ``name_changes``.

In [249]:
# retrieve manual corrections from csv file if they exist 
manual_corrects_df = pd.read_csv('data/manual_corrections.csv')
manual_corrects_dict = manual_corrects_df.to_dict(orient='index')
manual_corrects = {}
# add manual corrections to manual_corrects dictionary 
for correction in manual_corrects_dict.keys():
    manual_corrects[manual_corrects_dict[correction]['Unnamed: 0']] = [manual_corrects_dict[correction]['new first name'], manual_corrects_dict[correction]['new last name']]

print(manual_corrects)

{'henry mc clellen and henry': ['henry', 'mc clellen | henry'], 'william allison ex of mat mease': ['william', 'allison'], 'samuel ely and michael gellington esq': ['samuel | michael', 'ely | gellington'], 'michael schubert for st michael and zeus ': ['michael', 'schubert'], 'corporation for the relief of poor and distressed presbyterian ministers': ['corporation for the relief of poor and distressed presbyterian ministers', nan], 'corporation for relief of poor and distressed presbyterian ministers': ['corporation for relief of poor and distressed presbyterian ministers', nan], 'Nathaniel Appleton and other trustees of Judah Monis Legasy': ['Nathaniel', 'Appleton'], 'Gilbert Sutton John Voorhees Lawrence Vandiveer and Jacobus Vandiveer': ['Gilbert | John | Lawrence | Jacobus', 'Sutton | Voorhees | Vandiveer | Vandiveer'], 'Society for Relief of Poor Masters of ships  widows and children': ['Society for Relief of Poor Masters of ships  widows and children', nan], 'Robert Morris and Joh

In [250]:
# dictionary of manual changes i have to make 
changes = {
    'Henry Mc Clellen & Henry & co' : 'Henry Mc Clellen & Co'
}

conn_words = [' for ', ' of ', ' and '] # these are connector key words
corp_key_words = ('corporation', ' and co', ' and coy', ' and others', ' and several others', ' and heirs', ' and comp', ' and other trustees') # these are corporation key words

In [251]:
def handle_comp_name(row):        
    org_fname = str(row['to whom due | first name'])
    org_lname = str(row['to whom due | last name'])
    
    fname = str(row['to whom due | first name'])
    fname = fname.replace('&', 'and')
    fname = fname.replace('.', '')
    
    if fname in changes:
        fname = changes[fname]
    
    fname_l = str(fname).lower().strip()
    
    # check if string ends with co, coy, or others; if so, delete 
    for key_word in corp_key_words:
        if fname_l.endswith(key_word):
            print('index=' + str(row['Unnamed: 0']))
            print('old name=' + str(fname_l))      
            fname_corr = fname_l.split(key_word)
            print('corrected name=' + str(fname_corr[0])) 
            fname_corr = fname_corr[0]
            fname_sp = fname_corr.split()
            
            # only one name; put name into last name column 
            if len(fname_sp) == 1:
                row['to whom due | first name'] = ''
                row['to whom due | last name'] = fname_sp[0].capitalize()
                print('corrected name=' + str(fname_sp[0])) 
                print('new last name=' + str(fname_sp[0].capitalize()))
                
            # if there are is only a first name and a last name, put into respective columns
            elif len(fname_sp) == 2:
                row['to whom due | first name'] = fname_sp[0].capitalize()
                row['to whom due | last name'] = fname_sp[1].capitalize()
                print('new first name=' + str(fname_sp[0].capitalize()))
                print('new last name=' + str(fname_sp[1].capitalize()))
                
            # handles middle names; put middle names in last name column 
            elif len(fname_sp) == 3:
                row['to whom due | first name'] = fname_sp[0].capitalize() 
                row['to whom due | last name'] = fname_sp[1].capitalize() + ' ' + fname_sp[2].capitalize()
                print('new first name=' + str(fname_sp[0].capitalize()))
                print('new last name=' + str(fname_sp[1].capitalize() + ' ' + fname_sp[2].capitalize()))  
            # manually clean debt entries that have long names 
            else: 
                # check if name has already been manually cleaned
                if fname_corr in manual_corrects:
                    new_fname = manual_corrects[fname_corr][0]
                    new_lname = manual_corrects[fname_corr][1]
                else:
                    new_fname = input('new first name: ')
                    new_lname = input('new last name: ') 
                    manual_corrects[fname_corr] = [new_fname, new_lname]
                
                row['to whom due | first name'] = new_fname.capitalize()
                row['to whom due | last name'] = new_lname.capitalize()
                    
                print('new first name=' + str(new_fname.capitalize()))
                print('new last name=' + str(new_lname.capitalize()))  
                
            # record change 
            add_changes(row['to whom due | title'], row['to whom due | title'], org_fname, org_lname, 
                   row['to whom due | first name'], row['to whom due | last name'], 2, row['org_file'], row['org_index'])
            
            print('+------------------------------+')
        # if the name starts with any keyword: 'corporation for the relief of...'; manually change these names
        elif fname_l.startswith(key_word): 
            print('index=' + str(row['Unnamed: 0']))
            print('old name=' + str(fname_l))      
            
            # check if name has already been manually cleaned
            if fname_l in manual_corrects:
                new_fname = str(manual_corrects[fname_l][0])
                new_lname = str(manual_corrects[fname_l][1])
            else:
                new_fname = input('new first name: ')
                new_lname = input('new last name: ') 
                manual_corrects[fname_l] = [new_fname, new_lname]

            row['to whom due | first name'] = new_fname.capitalize()
            row['to whom due | last name'] = new_lname.capitalize()
            
            # record change 
            add_changes(row['to whom due | title'], row['to whom due | title'], org_fname, org_lname, 
                   row['to whom due | first name'], row['to whom due | last name'], 2, row['org_file'], row['org_index'])

            print('new first name=' + str(new_fname.capitalize()))
            print('new last name=' + str(new_lname.capitalize()))  
    
    return row

agg_debt = agg_debt.apply(lambda row: handle_comp_name(row), axis=1)

index=502
old name=henry wisner and co
corrected name=henry wisner
new first name=Henry
new last name=Wisner
+------------------------------+
index=503
old name=henry wisner and co
corrected name=henry wisner
new first name=Henry
new last name=Wisner
+------------------------------+
index=504
old name=henry wisner and co
corrected name=henry wisner
new first name=Henry
new last name=Wisner
+------------------------------+
index=505
old name=henry wisner and co
corrected name=henry wisner
new first name=Henry
new last name=Wisner
+------------------------------+
index=506
old name=henry wisner and co
corrected name=henry wisner
new first name=Henry
new last name=Wisner
+------------------------------+
index=507
old name=henry wisner and co
corrected name=henry wisner
new first name=Henry
new last name=Wisner
+------------------------------+
index=508
old name=henry wisner and co
corrected name=henry wisner
new first name=Henry
new last name=Wisner
+------------------------------+
index=

index=14731
old name=james glenn and co
corrected name=james glenn
new first name=James
new last name=Glenn
+------------------------------+
index=14733
old name=glenn mcclay and co
corrected name=glenn mcclay
new first name=Glenn
new last name=Mcclay
+------------------------------+
index=14984
old name=whitehead jones and co
corrected name=whitehead jones
new first name=Whitehead
new last name=Jones
+------------------------------+
index=15017
old name=william sharpley and co
corrected name=william sharpley
new first name=William
new last name=Sharpley
+------------------------------+
index=15018
old name=william sharpley and co
corrected name=william sharpley
new first name=William
new last name=Sharpley
+------------------------------+
index=15038
old name=james simpson and co
corrected name=james simpson
new first name=James
new last name=Simpson
+------------------------------+
index=15039
old name=james simpson and co
corrected name=james simpson
new first name=James
new last na

index=180781
old name=paris brothers and co
corrected name=paris brothers
new first name=Paris
new last name=Brothers
+------------------------------+
index=180782
old name=paris brothers and co
corrected name=paris brothers
new first name=Paris
new last name=Brothers
+------------------------------+
index=180801
old name=paris beith and co
corrected name=paris beith
new first name=Paris
new last name=Beith
+------------------------------+
index=180802
old name=paris beith and co
corrected name=paris beith
new first name=Paris
new last name=Beith
+------------------------------+
index=180803
old name=paris beith and co
corrected name=paris beith
new first name=Paris
new last name=Beith
+------------------------------+
index=180804
old name=paris beith and co
corrected name=paris beith
new first name=Paris
new last name=Beith
+------------------------------+
index=180805
old name=paris beith and co
corrected name=paris beith
new first name=Paris
new last name=Beith
+--------------------

index=200540
old name=sd george and comp
corrected name=sd george
new first name=Sd
new last name=George
+------------------------------+
index=200541
old name=sd george and comp
corrected name=sd george
new first name=Sd
new last name=George
+------------------------------+
index=200542
old name=sd george and comp
corrected name=sd george
new first name=Sd
new last name=George
+------------------------------+
index=200543
old name=sd george and comp
corrected name=sd george
new first name=Sd
new last name=George
+------------------------------+
index=200544
old name=sd george and comp
corrected name=sd george
new first name=Sd
new last name=George
+------------------------------+
index=200545
old name=sd george and comp
corrected name=sd george
new first name=Sd
new last name=George
+------------------------------+
index=200546
old name=sd george and comp
corrected name=sd george
new first name=Sd
new last name=George
+------------------------------+
index=200547
old name=sd george an

In [252]:
# checkup on name_changes
name_changes.head()

title_org  title_new     first_name_org last_name_org first_name_new  \
0        NaN        NaN  Henry Wisner & Co           nan          Henry   
1        NaN        NaN  Henry Wisner & Co           nan          Henry   
2        NaN        NaN  Henry Wisner & Co           nan          Henry   
3        NaN        NaN  Henry Wisner & Co           nan          Henry   
4        NaN        NaN  Henry Wisner & Co           nan          Henry   

  last_name_new  cleaning case                              file_loc  \
0        Wisner              2  liquidated_debt_certificates_NY.xlsx   
1        Wisner              2  liquidated_debt_certificates_NY.xlsx   
2        Wisner              2  liquidated_debt_certificates_NY.xlsx   
3        Wisner              2  liquidated_debt_certificates_NY.xlsx   
4        Wisner              2  liquidated_debt_certificates_NY.xlsx   

   org_index  
0        491  
1        492  
2        493  
3        494  
4        495

In [253]:
agg_debt['Unnamed: 0'] = agg_debt.index

In [254]:
agg_debt.rename(columns={'Unnamed: 0' : 'index'}, inplace=True)

## Cleaning Entries with Two Names

<b>Goal: </b>There are debt entries that have two names in a single cell: ```NY_2422: Messes Williamson & Beckman```. The plan is to split the name across the first name and last name columns. Note: I have to check naming conventions during thre 1700s. 

<b>Steps: </b>
1. Use string parsing to check if the name contains '&' or 'and' and split the string accordingly. 
2. Use the human name parser library to determine the first name and last names. 
3. Put each person's first name and last name in the respective columns, split by ```|``` to separate both individuals' names. 
4. Record change in ```name_changes```.

<b>Examples of different formats</b>
- James and Ash 
- William Miller and John Gamble

In [255]:
changes = {
    'van zandt & kittletas' : ['', 'van zandt | kittletas'],
    'trustees of & davids church':['trustees of & davids church', '']
}

In [256]:
# make sure all names are of type: str
agg_debt[['to whom due | first name', 'to whom due | last name']] = agg_debt[['to whom due | first name', 'to whom due | last name']].astype(str)

In [257]:
# Function to convert
def listToString(s):
 
    # initialize an empty string
    str1 = " "
 
    # return string
    return (str1.join(s))

In [258]:
def handle_two_name(row):
    org_fn = row['to whom due | first name']
    org_ln = row['to whom due | last name']
    
    org_fn_l = str(org_fn).lower()
        
    # remove extraneous information like 'for the estates of...'
    org_fn_l = org_fn_l.split(' for ')[0]

    # remove extraneous information like 'of the heirs of...'
    org_fn_l = org_fn_l.split(' of ')[0]

    # remove occupations: guardians, etc. 
    org_fn_l = org_fn_l.replace(' guardian', '')
    
    # check if there are two individuals, but check if there are more than 7 words (most likely a society)
    if ' and ' in org_fn_l and len(org_fn_l.split()) <= 7:   
        print('original name= ' + org_fn_l)
        
        # cleaning extraneous information can reveal there to be only one name
        #if ' and ' in org_fn_l:
        person1 = org_fn_l.split(' and ')[0]
        person2 = org_fn_l.split(' and ')[1]
        person1_sp = person1.split() 
        person2_sp = person2.split()

        # recapitalize people's names
        person1_sp = [i.title() for i in person1_sp]
        person2_sp = [i.title() for i in person2_sp]

        # if both individuals only have a last name; put both last names into last name column  ex. edward and joseph
        if len(person1_sp) == 1 and len(person2_sp) == 1:
            row['to whom due | first name'] = ''
            row['to whom due | last name'] = [person1_sp[0], person2_sp[0]] 
            
            print('new last name col (org)=' + listToString(row['to whom due | last name']))
        # if there are three separate last names; put all three into last name column: ex. vance caldwell and vance
        elif len(person1_sp) == 2 and len(person2_sp) == 1:
            row['to whom due | first name'] = ''
            row['to whom due | last name'] = [person1_sp[0], person1_sp[1], person2_sp[0]]
            print('new last name col=' + listToString(row['to whom due | last name']))
        # if both individuals belong to the same family; put names into respective cols: ex. peter and isaac wikoff  
        elif len(person1_sp) == 1 and len(person2_sp) == 2:
            row['to whom due | first name'] = [person1_sp[0], person2_sp[0]]
            row['to whom due | last name'] = person2_sp[1]
            print('new first name col=' + listToString(row['to whom due | first name']))
            print('new last name col=' + listToString(row['to whom due | last name']))
        # if both individuals are two completely different people with full names; ex. john doe and james hill
        elif len(person1_sp) == 2 and len(person2_sp) == 2:
            row['to whom due | first name'] = [person1_sp[0], person2_sp[0]]
            row['to whom due | last name'] = [person1_sp[1], person2_sp[1]]
            print('new first name col=' + listToString(row['to whom due | first name']))
            print('new last name col=' + listToString(row['to whom due | last name']))
        # if either individual has a middle name; group middle names with the last name; ex. john hill doe and james madison hill
        elif len(person1_sp) == 3 or len(person2_sp) == 3:
            row['to whom due | first name'] = [person1_sp[0], person2_sp[0]]
            # determine which individual has the middle name
            if len(person1_sp) == 3:
                person2_ln = ''
                if len(person2_sp) > 1:
                    person2_ln = person2_sp[1]
                
                row['to whom due | last name'] = [person1_sp[1] + ' ' + person1_sp[2], person2_ln]
                print('new last name col=' + listToString(row['to whom due | last name']))
            elif len(person2_sp) == 3:
                person1_ln = ''
                if len(person1_sp) > 1:
                    person1_ln = person1_sp[1]
                
                row['to whom due | last name'] = [person1_ln, person2_sp[1] + ' ' + person2_sp[2]]
                print('new last name col=' + listToString(row['to whom due | last name']))
            # both individuals have a middle name 
            else:
                row['to whom due | last name'] = [person1_sp[1] + ' ' + person1_sp[2], person2_sp[1] + ' ' + person2_sp[2]]
                print('new last name col=' + listToString(row['to whom due | last name']))
        
        # handle all other types of names manually
        else:
            if org_fn in manual_corrects:
                new_fname = str(manual_corrects[org_fn][0])
                new_lname = str(manual_corrects[org_fn][1])
            else:
                new_fname = input('new first name: ')
                new_lname = input('new last name: ') 
                manual_corrects[org_fn] = [new_fname, new_lname]

            row['to whom due | first name'] = new_fname.capitalize()
            row['to whom due | last name'] = new_lname.capitalize()
        
        # record change 
        add_changes(row['to whom due | title'], row['to whom due | title'], org_fn, org_ln, 
                row['to whom due | first name'], row['to whom due | last name'], 3, row['org_file'], row['org_index'])
            
        print('+------------------------------+')
    # might be a corporation or many names; manually fix
    elif ' and ' in org_fn_l and len(org_fn_l.split()) > 7:
        print('original name= ' + org_fn_l)
         # check if name has already been manually cleaned
        if org_fn in manual_corrects:
            new_fname = str(manual_corrects[org_fn][0])
            new_lname = str(manual_corrects[org_fn][1])
        else:
            new_fname = input('new first name: ')
            new_lname = input('new last name: ') 
            manual_corrects[org_fn] = [new_fname, new_lname]

        row['to whom due | first name'] = new_fname.capitalize()
        row['to whom due | last name'] = new_lname.capitalize()
        
        # record change 
        add_changes(row['to whom due | title'], row['to whom due | title'], org_fn, org_ln, 
                row['to whom due | first name'], row['to whom due | last name'], 3, row['org_file'], row['org_index'])

        print('new first name col=' + listToString(row['to whom due | first name']))
        print('new last name col=' + listToString(row['to whom due | last name']))

        print('+------------------------------+')
    
    # capitalize the names properly 
    row['to whom due | first name'] = row['to whom due | first name']
    row['to whom due | last name'] = row['to whom due | last name']
        
    return row

agg_debt = agg_debt.apply(lambda row: handle_two_name(row), axis=1)

original name= daniel and john
new last name col (org)=Daniel John
+------------------------------+
original name= hermon and brimmer
new last name col (org)=Hermon Brimmer
+------------------------------+
original name= gordon and mcclemments
new last name col (org)=Gordon Mcclemments
+------------------------------+
original name= gordon and mcclemments
new last name col (org)=Gordon Mcclemments
+------------------------------+
original name= wilson and fury
new last name col (org)=Wilson Fury
+------------------------------+
original name= wilson and fury
new last name col (org)=Wilson Fury
+------------------------------+
original name= wilson and fury
new last name col (org)=Wilson Fury
+------------------------------+
original name= wilson and fury
new last name col (org)=Wilson Fury
+------------------------------+
original name= edward and joseph
new last name col (org)=Edward Joseph
+------------------------------+
original name= daniel j adams and peter adams
new last name co

original name= nathaniel appleton and other trustees
new first name col=Nathaniel Other
new last name col=Appleton Trustees
+------------------------------+
original name= riggs  dairs and humphrey
new last name col=Riggs Dairs Humphrey
+------------------------------+
original name= henry mcclellen  and henry
new last name col=Henry Mcclellen Henry
+------------------------------+
original name= henry mcclellen  and henry
new last name col=Henry Mcclellen Henry
+------------------------------+
original name= henry mcclellen  and henry
new last name col=Henry Mcclellen Henry
+------------------------------+
original name= henry mcclellen  and henry
new last name col=Henry Mcclellen Henry
+------------------------------+
original name= henry mcclellen  and henry
new last name col=Henry Mcclellen Henry
+------------------------------+
original name= henry mcclellen  and henry
new last name col=Henry Mcclellen Henry
+------------------------------+
original name= henry mcclellen  and henr

original name= john stevens and william burnett
new first name col=John William
new last name col=Stevens Burnett
+------------------------------+
original name= john stevens and william burnett
new first name col=John William
new last name col=Stevens Burnett
+------------------------------+
original name= john stevens and william burnett
new first name col=John William
new last name col=Stevens Burnett
+------------------------------+
original name= john stevens and william burnett
new first name col=John William
new last name col=Stevens Burnett
+------------------------------+
original name= stephen ford and canfield
new last name col=Stephen Ford Canfield
+------------------------------+
original name= stephen ford and canfield
new last name col=Stephen Ford Canfield
+------------------------------+
original name= stephen ford and canfield
new last name col=Stephen Ford Canfield
+------------------------------+
original name= forman and hunt
new last name col (org)=Forman Hunt
+--

original name= john smith and james mcdonald
new first name col=John James
new last name col=Smith Mcdonald
+------------------------------+
original name= will robinson and sons
new last name col=Will Robinson Sons
+------------------------------+
original name= vance caldwell and vance
new last name col=Vance Caldwell Vance
+------------------------------+
original name= vance caldwell and vance
new last name col=Vance Caldwell Vance
+------------------------------+
original name= vance caldwell and vance
new last name col=Vance Caldwell Vance
+------------------------------+
original name= vance caldwell and vance
new last name col=Vance Caldwell Vance
+------------------------------+
original name= vance caldwell and vance
new last name col=Vance Caldwell Vance
+------------------------------+
original name= vance caldwell and vance
new last name col=Vance Caldwell Vance
+------------------------------+
original name= vance caldwell and vance
new last name col=Vance Caldwell Vance


original name= ferrason and pocy
new last name col (org)=Ferrason Pocy
+------------------------------+
original name= ferrason and pocy
new last name col (org)=Ferrason Pocy
+------------------------------+
original name= ferrason and pocy
new last name col (org)=Ferrason Pocy
+------------------------------+
original name= terrason and pory
new last name col (org)=Terrason Pory
+------------------------------+
original name= terrason and pory
new last name col (org)=Terrason Pory
+------------------------------+
original name= ferrason and pocy
new last name col (org)=Ferrason Pocy
+------------------------------+
original name= sam and rob
new last name col (org)=Sam Rob
+------------------------------+
original name= henry and thomas brown
new first name col=Henry Thomas
new last name col=B r o w n
+------------------------------+
original name= henry and thomas brown
new first name col=Henry Thomas
new last name col=B r o w n
+------------------------------+
original name= henry a

+------------------------------+
original name= wilkins and gassaway
new last name col (org)=Wilkins Gassaway
+------------------------------+
original name= wilkins and gassaway
new last name col (org)=Wilkins Gassaway
+------------------------------+
original name= wilkins and gassaway
new last name col (org)=Wilkins Gassaway
+------------------------------+
original name= wilkins and gassaway
new last name col (org)=Wilkins Gassaway
+------------------------------+
original name= wilkins and gassaway
new last name col (org)=Wilkins Gassaway
+------------------------------+
original name= wilkins and gassaway
new last name col (org)=Wilkins Gassaway
+------------------------------+
original name= wilkins and gassaway
new last name col (org)=Wilkins Gassaway
+------------------------------+
original name= wilkins and gassaway
new last name col (org)=Wilkins Gassaway
+------------------------------+
original name= wilkins and gassaway
new last name col (org)=Wilkins Gassaway
+---------

In [259]:
# save manual corrections 
manual_corrects_df = pd.DataFrame.from_dict(manual_corrects, orient='index') 
manual_corrects_df.columns = ['new first name', 'new last name']
manual_corrects_df.to_csv('data/manual_corrections.csv')

In [260]:
# if there are debt entries with multiple individuals, split them into their own rows
agg_debt = agg_debt.explode('to whom due | first name')
agg_debt = agg_debt.explode('to whom due | last name')
# reindex
agg_debt['index'] = agg_debt.index

In [261]:
# checkup on name_changes
name_changes.tail()

title_org  title_new                        first_name_org  \
1451        NaN        NaN                   Russell and Gilmour   
1452        NaN        NaN                   Russell and Gilmour   
1453        NaN        NaN  Francis Fair Brother and Allen Luynn   
1454        NaN        NaN  Francis Fair Brother and Allen Luynn   
1455        NaN        NaN                     Hoov and Harrison   

     last_name_org    first_name_new          last_name_new  cleaning case  \
1451           nan                       [Russell, Gilmour]              3   
1452           nan                       [Russell, Gilmour]              3   
1453           nan  [Francis, Allen]  [Fair Brother, Luynn]              3   
1454           nan  [Francis, Allen]  [Fair Brother, Luynn]              3   
1455           nan                         [Hoov, Harrison]              3   

                                      file_loc  org_index  
1451    loan_office_certificates_9_states.xlsx      77446  
1452    loan_office_certificates_9_states.xlsx      77447  
1453    loan_office_certificates_9_states.xlsx      77900  
1454    loan_office_certificates_9_states.xlsx      77901  
1455  Marine_Liquidated_Debt_Certificates.xlsx        764

In [262]:
agg_debt

index letter  date of the certificate | month  \
0            0      C                              8.0   
1            1      L                              8.0   
2            2      G                              8.0   
3            3      C                              9.0   
4            4      B                              9.0   
...        ...    ...                              ...   
311670  311670      P                              5.0   
311671  311671      H                              4.0   
311671  311671      H                              4.0   
311672  311672    NaN                              NaN   
311673  311673    NaN                              NaN   

        date of the certificate | day  date of the certificate | year  \
0                                27.0                          1783.0   
1                                27.0                          1783.0   
2                                27.0                          1783.0   
3                                 2.0                          1783.0   
4                                 2.0                          1783.0   
...                               ...                             ...   
311670                           28.0                          1789.0   
311671                           28.0                          1789.0   
311671                           28.0                          1789.0   
311672                            NaN                             NaN   
311673                            NaN                             NaN   

       to whom due | first name to whom due | last name to whom due | title  \
0                     Elizabeth                  Lowell                 NaN   
1                        Joshua                Brackett                 Jun   
2                        Joshua                Brackett                 NaN   
3                      Phillips                   White                 Esq   
4                       William                   White                 NaN   
...                         ...                     ...                 ...   
311670                    James                   Odell                 NaN   
311671                                             Hoov                 NaN   
311671                                         Harrison                 NaN   
311672                      nan                     nan                 NaN   
311673                      nan                     nan                 NaN   

        time when the debt became due | month  \
0                                         4.0   
1                                         4.0   
2                                         4.0   
3                                         4.0   
4                                         4.0   
...                                       ...   
311670                                    1.0   
311671                                    6.0   
311671                                    6.0   
311672                                    NaN   
311673                                    NaN   

       time when the debt became due | day  ... amount | 10th  exchange  \
0                                     16.0  ...           NaN       NaN   
1                                     16.0  ...           NaN       NaN   
2                                     16.0  ...           NaN       NaN   
3                                     16.0  ...           NaN       NaN   
4                                     16.0  ...           NaN       NaN   
...                                    ...  ...           ...       ...   
311670                                 1.0  ...           NaN       NaN   
311671                                 1.0  ...           NaN       NaN   
311671                                 1.0  ...           NaN       NaN   
311672                                 NaN  ...           NaN       NaN   
311673                                 NaN  ...           NaN       NaN 

In [263]:
df = pd.DataFrame({'A': [[0, 1, 2], 'foo', [], [3, 4]],
                   'B': [1, 2, 3, 4],
                   'C': [['a', 'b', 'c'], np.nan, [], ['d', 'e']]})
df

A  B          C
0  [0, 1, 2]  1  [a, b, c]
1        foo  2        NaN
2         []  3         []
3     [3, 4]  4     [d, e]

In [264]:
df = df.explode(list('AC'))
df['index'] = df.index

In [265]:
df

A  B    C  index
0    0  1    a      0
0    1  1    b      0
0    2  1    c      0
1  foo  2  NaN      1
2  NaN  3  NaN      2
3    3  4    d      3
3    4  4    e      3

In [266]:
column_map = {col: "first" for col in df.columns}
column_map["A"] = lambda x: x.tolist() if len(x) > 1 else x
column_map["C"] = lambda x: x.tolist() if len(x) > 1 else x

In [267]:
df = (df.groupby(['index'])
      .agg(column_map).reset_index(drop=True))
df

A  B          C  index
0  [0, 1, 2]  1  [a, b, c]      0
1        foo  2        NaN      1
2        NaN  3        NaN      2
3     [3, 4]  4     [d, e]      3

## Handle Abbreviations of a Name

<b>Goal: </b>There are individuals who have a handwritten abbreviation of a name in their debt entry. Thanks to Chris, he found a website with all these [abbreviations](https://hull-awe.org.uk/index.php/Conventional_abbreviations_for_forenames). 

<b>Steps: </b>
1. Copy and past the name abbreviations from the website into a dictionary. 
2. Iterate through each row in the dataframe.
3. Check if the name is an abbreviation and change accordingly. 
4. Record changes. 


In [268]:
abbreviations = {
    'And':'Andrew', 'Ant':'Anthony', 'Bart':'Bartholomew', 'Cha':'Charles', 'Dor':'Dorothy', 'Dot':'Dorothy', 'Doth':'Dorothy',
    'Edw':'Edward', 'Eliz':'Elizabeth', 'Geo':'George', 'H':'Henry', 'Herb':'Herbert', 'Ja':'James', 'Jn':'John', 'Marg':'Margaret', 
    'Mich':'Michael', 'Pat': 'Patrick', 'Rich':'Richard', 'Tho':'Thomas', 'W':'William', 'Will\'m':'William'
}

In [269]:
def handle_abbreviations(row):
    fn = str(row['to whom due | first name'])
    if fn in abbreviations:
        row['to whom due | first name'] = abbreviations[fn]
        # record changes
        add_changes(row['to whom due | title'], row['to whom due | title'], fn, 
                    row['to whom due | last name'], row['to whom due | first name'], 
                    row['to whom due | last name'], 5, row['org_file'], row['org_index'])
    
    return row

agg_debt = agg_debt.apply(lambda row: handle_abbreviations(row), axis=1)

In [270]:
# checkup on name_changes
name_changes.tail()

title_org title_new first_name_org last_name_org first_name_new  \
1627       NaN       NaN             Jn  Gallaher Esq           John   
1628       NaN       NaN           Rich      Thompson        Richard   
1629       NaN       NaN           Rich      Thompson        Richard   
1630       NaN       NaN           Rich      Thompson        Richard   
1631       NaN       NaN           Rich      Thompson        Richard   

     last_name_new  cleaning case                                file_loc  \
1627  Gallaher Esq              5  loan_office_certificates_9_states.xlsx   
1628      Thompson              5  loan_office_certificates_9_states.xlsx   
1629      Thompson              5  loan_office_certificates_9_states.xlsx   
1630      Thompson              5  loan_office_certificates_9_states.xlsx   
1631      Thompson              5  loan_office_certificates_9_states.xlsx   

      org_index  
1627      62583  
1628      69947  
1629      69948  
1630      69949  
1631      69950

## Grouping Consecutive Names - Liam

In [271]:
og_df = agg_debt

In [273]:
#Loop that covers Objective 1 (aggregate data files)
def element_to_int(ele): # handles all kinds of Nans (returns 0 for nans)
    if type(ele) == np.float64:
        ele = round(ele)
    if ele == np.nan: return 0
    if str(ele) == "nan": return 0
    return round(np.float64(ele))

def get_dollar(row): #gets the dollar from a row by checking both dollar columns
    dollar = 0
    ninety = 0
    #if dollar (90th) is a decimal, then split it
    if '.' in str(element_to_int(row[11])): # "amount | dollar"
        split = str(element_to_int(row[11])).split(".")
        dollar, ninety = element_to_int(split[0]), element_to_int(split[1])
    elif str(row[11]) == "": # "amount | dollar"
        if '.' in str(element_to_int(row[24])): # "amount | specie"
            split = str(element_to_int(row[24])).split() # "amount | specie"
            dollar, ninety = element_to_int(split[0]), element_to_int(split[1])
    else:
        dollar = element_to_int(row[11]) # "amount | dollar"
        ninety = element_to_int(row[12]) # "amount | 90th"
    return float(str(dollar) + "." + str(ninety))

def new_tup(old_row, new_dol, new_ninety, new_title): # returns a new tuple, specifically for totaled debt amounts (since you can't assign new values in tuples)
    return (old_row[0], old_row[1], old_row[2], old_row[3], old_row[4], old_row[5], old_row[6],
            new_title, old_row[8], old_row[9], old_row[10], new_dol, new_ninety, old_row[13],
            old_row[14], old_row[15], old_row[16], old_row[17], old_row[18], old_row[19],
            old_row[20], old_row[21], old_row[22], old_row[23], old_row[24], old_row[25],
            old_row[26], old_row[27], old_row[28], old_row[29], old_row[30], old_row[31], old_row[32])

agg_df = pd.DataFrame(columns=og_df.columns)
last_f, last_l, last_t = "", "", ""
last_row = None
#save the sum of money
current_sum = 0
for row in og_df.itertuples(name=None, index=False): #main processing function
    fname, lname = str(row[5]).strip(), str(row[6]).strip()
    last_t = last_t if str(row[7]).strip().lower() == "nan" else str(row[7]).strip()
    if fname == last_f and lname == last_l: #If the next name is the same as the last one, add onto the amount
        dol = get_dollar(row)
        print(f"adding {dol} to {fname} {lname}'s total")
        current_sum += dol
    else: #If the next name is not the same as the last one:
        if current_sum > 0: #If the sum is more than 0 (ie. this is the end of consecutive same-name entries), then only add this on
            print(f"{last_row[5]} {last_row[6]} is consecutively owed {current_sum}")
            #consecutive has ended
            split = str(current_sum).split(".")
            agg_df.loc[len(agg_df.index)] = new_tup(last_row, int(split[0]), int(split[1]), last_t if last_t != "" else "")
            current_sum = 0
        else: #If the sum is not more than 0 (ie. this is one unique entry, add it on now)
            #Normal
            agg_df.loc[len(agg_df.index)] = last_row
    last_f, last_l = fname, lname
    last_row = row

adding 27.45 to Joshua Brackett's total
Joshua Brackett is consecutively owed 27.45
adding 75.67 to Henry Dearborn's total
Henry Dearborn is consecutively owed 75.67
adding 7.45 to Amos Morrill's total
Amos Morrill is consecutively owed 7.45
adding 590.65 to Joseph Wells's total
adding 186.8 to Joseph Wells's total
Joseph Wells is consecutively owed 777.45
adding 186.45 to Joseph Wells's total
adding 329.5 to Joseph Wells's total
Joseph Wells is consecutively owed 515.95
adding 64.67 to Joseph Wells's total
Joseph Wells is consecutively owed 64.67
adding 1108.6 to Joseph Milnor's total
adding 339.6 to Joseph Milnor's total
Joseph Milnor is consecutively owed 1448.1999999999998
adding 277.48 to Furman & Hunt nan's total
adding 111.6 to Furman & Hunt nan's total
Furman & Hunt nan is consecutively owed 389.08000000000004
adding 119.54 to Abner Hunt's total
Abner Hunt is consecutively owed 119.54
adding 297.2 to Stacey Potts's total
Stacey Potts is consecutively owed 297.2
adding 26.0 to W

adding 188.0 to Varnal Hunt's total
Varnal Hunt is consecutively owed 188.0
adding 52.0 to Nich Hight's total
adding 284.0 to Nich Hight's total
Nich Hight is consecutively owed 336.0
adding 25.0 to John Snider's total
adding 205.6 to John Snider's total
adding 1.54 to John Snider's total
John Snider is consecutively owed 232.14
adding 427.5 to Thomas Kinney's total
Thomas Kinney is consecutively owed 427.5
adding 106.6 to Amit Sarkar's total
Amit Sarkar is consecutively owed 106.6
adding 123.0 to Samuel Hill's total
adding 60.0 to Samuel Hill's total
Samuel Hill is consecutively owed 183.0
adding 140.3 to Joseph Broadhurst's total
adding 400.0 to Joseph Broadhurst's total
adding 32.0 to Joseph Broadhurst's total
Joseph Broadhurst is consecutively owed 572.3
adding 116.0 to Moses Moore's total
adding 73.9 to Moses Moore's total
adding 72.9 to Moses Moore's total
Moses Moore is consecutively owed 262.8
adding 380.0 to Daniel Yard's total
Daniel Yard is consecutively owed 380.0
adding 64

adding 177.24 to Mindert Garrabrants's total
adding 88.57 to Mindert Garrabrants's total
adding 88.57 to Mindert Garrabrants's total
Mindert Garrabrants is consecutively owed 354.38
adding 146.3 to John VanHorne's total
adding 73.15 to John VanHorne's total
adding 73.15 to John VanHorne's total
John VanHorne is consecutively owed 292.6
adding 155.81 to Gilm Outwater's total
adding 77.85 to Gilm Outwater's total
adding 77.86 to Gilm Outwater's total
adding 0.0 to Gilm Outwater's total
adding 122.78 to Gilm Outwater's total
adding 61.39 to Gilm Outwater's total
adding 61.39 to Gilm Outwater's total
Gilm Outwater is consecutively owed 557.0799999999999
adding 74.84 to Gar Van Ripen's total
adding 37.42 to Gar Van Ripen's total
adding 37.42 to Gar Van Ripen's total
Gar Van Ripen is consecutively owed 149.68
adding 42.6 to Levinus Winne's total
adding 21.3 to Levinus Winne's total
adding 21.3 to Levinus Winne's total
Levinus Winne is consecutively owed 85.2
adding 40.72 to Johannis Winne's 

adding 46.15 to Jonathan Willis's total
Jonathan Willis is consecutively owed 46.15
adding 0.0 to Ephraim Darby's total
adding 0.0 to Ephraim Darby's total
adding 31.15 to Ephraim Darby's total
adding 224.49 to Ephraim Darby's total
adding 80.0 to Ephraim Darby's total
Ephraim Darby is consecutively owed 335.64
adding 103.86 to Thomas Anderson's total
adding 42.12 to Thomas Anderson's total
Thomas Anderson is consecutively owed 145.98
adding 150.0 to Silas Burnet's total
adding 0.0 to Silas Burnet's total
Silas Burnet is consecutively owed 150.0
adding 173.71 to John Maxwell's total
John Maxwell is consecutively owed 173.71
adding 73.88 to Adam Hawke's total
Adam Hawke is consecutively owed 73.88
adding 9.24 to Joseph Miller's total
Joseph Miller is consecutively owed 9.24
adding 0.0 to Nath Horton's total
adding 37.3 to Cornelius Ackerman's total
Cornelius Ackerman is consecutively owed 37.3
adding 57.3 to Peter Cole's total
Peter Cole is consecutively owed 57.3
adding 18.88 to Hendri

adding 0.0 to Aaron Harrison's total
adding 0.0 to Aaron Harrison's total
adding 11.88 to John Terrill's total
John Terrill is consecutively owed 11.88
adding 0.0 to John Ross's total
adding 0.0 to John Ross's total
adding 16.6 to Sylvenus Pearson's total
adding 0.0 to Sylvenus Pearson's total
Sylvenus Pearson is consecutively owed 16.6
adding 0.0 to Joseph Tomkins's total
adding 0.0 to Joseph Tomkins's total
adding 66.6 to Joseph Tomkins's total
adding 43.63 to Joseph Tomkins's total
Joseph Tomkins is consecutively owed 110.22999999999999
adding 0.0 to David Tichenor's total
adding 5.67 to Aaron Ogden's total
adding 12.45 to Aaron Ogden's total
Aaron Ogden is consecutively owed 18.119999999999997
adding 133.75 to Usal Willson's total
adding 0.0 to Usal Willson's total
Usal Willson is consecutively owed 133.75
adding 1022.89 to Elias Boudinot's total
adding 765.39 to Elias Boudinot's total
Elias Boudinot  is consecutively owed 1788.28
adding 19.5 to David Day's total
David Day is conse

...

adding 400.0 to William Owen's total
William Owen is consecutively owed 400.0
adding 3000.0 to John Ingerhowz's total
John Ingerhowz is consecutively owed 3000.0
adding 1000.0 to William Molineaux's total
adding 1000.0 to William Molineaux's total
William Molineaux is consecutively owed 2000.0
adding 1000.0 to John Fairfield's total
John Fairfield is consecutively owed 1000.0
adding 10000.0 to Jonathan Williams's total
adding 5000.0 to Jonathan Williams's total
adding 5000.0 to Jonathan Williams's total
adding 5000.0 to Jonathan Williams's total
Jonathan Williams is consecutively owed 25000.0
adding 5000.0 to William Foster's total
adding 5000.0 to William Foster's total
adding 5000.0 to William Foster's total
adding 5000.0 to William Foster's total
William Foster is consecutively owed 20000.0
adding 10000.0 to Jonathan Williams's total
adding 4000.0 to Jonathan Williams's total
Jonathan Williams is consecutively owed 14000.0
adding 5000.0 to Ellis Gray's total
Ellis Gray is consecutiv

adding 1000.0 to William Foster's total
William Foster is consecutively owed 1000.0
adding 600.0 to Mary Wilson's total
Mary Wilson is consecutively owed 600.0
adding 500.0 to Joseph Barnard's total
adding 500.0 to Joseph Barnard's total
Joseph Barnard is consecutively owed 1000.0
adding 200.0 to John Walley's total
John Walley is consecutively owed 200.0
adding 2000.0 to Joshua Prentiss's total
Joshua Prentiss is consecutively owed 2000.0
adding 600.0 to Samuel Salisbury's total
Samuel Salisbury is consecutively owed 600.0
adding 500.0 to Elizabeth Marston's total
Elizabeth Marston is consecutively owed 500.0
adding 400.0 to Moses Sargent's total
Moses Sargent is consecutively owed 400.0
adding 2000.0 to Daniel Sargent's total
adding 2000.0 to Daniel Sargent's total
adding 2000.0 to Daniel Sargent's total
adding 2000.0 to Daniel Sargent's total
adding 2000.0 to Daniel Sargent's total
Daniel Sargent is consecutively owed 10000.0
adding 400.0 to Stephen Dutch's total
adding 400.0 to Ste

adding 300.0 to John Green's total
John Green is consecutively owed 300.0
adding 2000.0 to Daniel Boyer's total
Daniel Boyer is consecutively owed 2000.0
adding 3000.0 to John Rowe's total
John Rowe is consecutively owed 3000.0
adding 3000.0 to Thomas Walley's total
adding 3000.0 to Thomas Walley's total
Thomas Walley is consecutively owed 6000.0
adding 1000.0 to Richard Salter's total
Richard Salter is consecutively owed 1000.0
adding 600.0 to Jonathan Ropes's total
Jonathan Ropes is consecutively owed 600.0
adding 500.0 to Thomas Walley's total
adding 500.0 to Thomas Walley's total
adding 500.0 to Thomas Walley's total
Thomas Walley is consecutively owed 1500.0
adding 400.0 to Richard Salter's total
Richard Salter is consecutively owed 400.0
adding 400.0 to Samuel Clap's total
Samuel Clap is consecutively owed 400.0
adding 300.0 to Noah Sweat's total
Noah Sweat is consecutively owed 300.0
adding 300.0 to Samuel Clap's total
adding 300.0 to Samuel Clap's total
adding 300.0 to Samuel C

adding 10000.0 to William Scott's total
adding 10000.0 to William Scott's total
adding 10000.0 to William Scott's total
adding 2000.0 to William Scott's total
William Scott is consecutively owed 32000.0
adding 2000.0 to Jonathan Hastings's total
Jonathan Hastings is consecutively owed 2000.0
adding 300.0 to Jonathan Hastings's total
Jonathan Hastings is consecutively owed 300.0
adding 5000.0 to Edward Tuckerman's total
adding 5000.0 to Edward Tuckerman's total
Edward Tuckerman is consecutively owed 10000.0
adding 200.0 to Joseph Montfort's total
Joseph Montfort is consecutively owed 200.0
adding 300.0 to Israel Bartlett's total
Israel Bartlett is consecutively owed 300.0
adding 300.0 to Samuel Butterfield's total
Samuel Butterfield is consecutively owed 300.0
adding 400.0 to Mary Boardman's total
Mary Boardman is consecutively owed 400.0
adding 400.0 to Holten Johnson's total
Holten Johnson is consecutively owed 400.0
adding 500.0 to Samuel Phillips's total
Samuel Phillips is consecuti

KeyboardInterrupt: 

In [ ]:
agg_df.tail()

In [ ]:
agg_debt = agg_df

In [ ]:
agg_debt.to_csv('data/agg_debt_grouped.csv') # save 

In [4]:
agg_debt = pd.read_csv('data/agg_debt_grouped.csv')

C:\Users\david\AppData\Local\Temp\ipykernel_46956\953087625.py:1: DtypeWarning: Columns (2,10,11,13,15,16,20,21,22,25,32) have mixed types. Specify dtype option on import or set low_memory=False.
  agg_debt = pd.read_csv('data/agg_debt_grouped.csv')


In [5]:
agg_debt.head()

Unnamed: 0  index letter  date of the certificate | month  \
0           0    NaN    NaN                              NaN   
1           1    0.0      C                              8.0   
2           2    2.0      G                              8.0   
3           3    3.0      C                              9.0   
4           4    4.0      B                              9.0   

   date of the certificate | day  date of the certificate | year  \
0                            NaN                             NaN   
1                           27.0                          1783.0   
2                           27.0                          1783.0   
3                            2.0                          1783.0   
4                            2.0                          1783.0   

  to whom due | first name to whom due | last name to whom due | title  \
0                      NaN                     NaN                 NaN   
1                Elizabeth                  Lowell                 NaN   
2                   Joshua                Brackett                 Esq   
3                 Phillips                   White                 Esq   
4                  William                   White                 NaN   

   time when the debt became due | month  ... amount | 10th exchange  \
0                                    NaN  ...           NaN      NaN   
1                                    4.0  ...           NaN      NaN   
2                                    4.0  ...           NaN      NaN   
3                                    4.0  ...           NaN      NaN   
4                                    4.0  ...           NaN      NaN   

   amount in specie | dollars amount in specie | cents  amount | 8th  \
0                         NaN                      NaN           NaN   
1                         NaN                      NaN           NaN   
2                         NaN                      NaN           NaN   
3                         NaN                      NaN           NaN   
4                         NaN                      NaN           NaN   

  delivered | month delivered | day delivered | year total dollars | notes  \
0               NaN             NaN              NaN                   NaN   
1               NaN             NaN              NaN                   NaN   
2               NaN             NaN              NaN                   NaN   
3               NaN             NaN              NaN                   NaN   
4               NaN             NaN              NaN                   NaN   

   total dollars | notes.1  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  

[5 rows x 34 columns]

## Standardizing Names

<b>Goal: </b>Multiple different spellings of a name can be referring to the same identity. We will use a phonetics library and Ancestry to fix this. An example: ```David Schaffer``` and ```David Schafer``` from `MA`. 

<b>Steps: </b>
1. Login to Emory's Ancestry subscription 
2. Iterate through ```agg_debt```, through each debt entry. 
3. Use a combination of phonetics fuzzy string matching and normal fuzzy string matching to determine if two names from a state are similar.  
4. Search each name in Ancestry: Edit URL (state and person's name). 
5. Check if there are any results for both person's name:
    - Yes: Check if one spelling of the name appears for both individuals (that's most likely the correct spelling of that name) 
    - No: Leave entries as two separate entries. 
6. Record name change in ```fixes``` list (save ```fixes``` as ```out.csv``` too). 
7. Run ```agg_debt``` through ```fixes```, making changes as necessary. 
8. Save ```agg_debt``` as a new .csv file.

<b style="color: red;">Note: Runtime is long. This is due to the fact there are over 200,000 debt entries and accessing Ancestry takes time too. </b>


In [6]:
# import necessary fuzzy string libraries 
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.support.expected_conditions import element_to_be_clickable, presence_of_element_located
from selenium.webdriver.support.wait import WebDriverWait
from selenium.common.exceptions import NoSuchElementException
from phonetics import metaphone
from rapidfuzz import fuzz
from joblib import Parallel, delayed, cpu_count
from itertools import zip_longest
import time 
import getpass

In [7]:
# options
options = Options()
options.add_argument('--headless')
options.add_argument("--window-size=1000,1000")
options.add_argument('--disable-blink-features=AutomationControlled')
options.add_argument('--no-sandbox')   

In [8]:
# install driver
'''
driver = webdriver.Chrome(service=Service(ChromeDriverManager(version='114.0.5735.16').install()), options=options)
wait = WebDriverWait(driver, 30)
'''

"\ndriver = webdriver.Chrome(service=Service(ChromeDriverManager(version='114.0.5735.16').install()), options=options)\nwait = WebDriverWait(driver, 30)\n"

In [9]:
'''
# login to emory ancestry 
driver.get('https://guides.libraries.emory.edu/ALE')
login_btn_xpath = '/html/body/main/div/div/div/a'
wait.until(element_to_be_clickable((By.XPATH, login_btn_xpath))).click()

# input login information and click 'login'
netid_xpath = '/html/body/div[1]/div[2]/section/div[1]/div/form/fieldset/div[1]/input'
password_xpath = '/html/body/div[1]/div[2]/section/div[1]/div/form/fieldset/div[2]/input'
username = input('username: ')
password = getpass.getpass(prompt='password: ')
netid_input = wait.until(element_to_be_clickable((By.XPATH, netid_xpath)))
netid_input.click()
netid_input.send_keys(username)
pass_input = wait.until(element_to_be_clickable((By.XPATH, password_xpath)))
pass_input.click()
pass_input.send_keys(password)

login_btn_xpath = '/html/body/div[1]/div[2]/section/div[1]/div/form/fieldset/div[3]/button'
wait.until(element_to_be_clickable((By.XPATH, login_btn_xpath))).click()
time.sleep(1)

driver.get('https://www.ancestrylibrary.com/search/collections/5058/')
'''

"\n# login to emory ancestry \ndriver.get('https://guides.libraries.emory.edu/ALE')\nlogin_btn_xpath = '/html/body/main/div/div/div/a'\nwait.until(element_to_be_clickable((By.XPATH, login_btn_xpath))).click()\n\n# input login information and click 'login'\nnetid_xpath = '/html/body/div[1]/div[2]/section/div[1]/div/form/fieldset/div[1]/input'\npassword_xpath = '/html/body/div[1]/div[2]/section/div[1]/div/form/fieldset/div[2]/input'\nusername = input('username: ')\npassword = getpass.getpass(prompt='password: ')\nnetid_input = wait.until(element_to_be_clickable((By.XPATH, netid_xpath)))\nnetid_input.click()\nnetid_input.send_keys(username)\npass_input = wait.until(element_to_be_clickable((By.XPATH, password_xpath)))\npass_input.click()\npass_input.send_keys(password)\n\nlogin_btn_xpath = '/html/body/div[1]/div[2]/section/div[1]/div/form/fieldset/div[3]/button'\nwait.until(element_to_be_clickable((By.XPATH, login_btn_xpath))).click()\ntime.sleep(1)\n\ndriver.get('https://www.ancestrylibra

In [10]:
'''
Find out what states are in the agg_debt dataframe - Helps with finding Ancestry urls 
Note:
- CS most likely stands for congress: Hazen's regiment 
- F probably stands for 'foreign' officers: most likely France
'''
agg_debt.state.unique()

array([nan, 'nh', 'nj', 'ny', 'ma', 'de', 'ct', 'va', 'pa', 'md', 'nc',
       'cs', 'ga', 'ri', 'f'], dtype=object)

In [11]:
# voter records and censuses available for every state 
records = {
    'nh':['https://www.ancestrylibrary.com/search/collections/5058/'],
    'nj':['https://www.ancestrylibrary.com/search/collections/2234/', 
          'https://www.ancestrylibrary.com/search/collections/3562/'],
    'ny':['https://www.ancestrylibrary.com/search/collections/5058/'],
    'ma':['https://www.ancestrylibrary.com/search/collections/5058/'], 
    'ct':['https://www.ancestrylibrary.com/search/collections/5058/'], 
    'va':['https://www.ancestrylibrary.com/search/collections/2234/', 
         'https://www.ancestrylibrary.com/search/collections/3578/'], 
    'pa':['https://www.ancestrylibrary.com/search/collections/2702/',
         'https://www.ancestrylibrary.com/search/collections/2234/',
         'https://www.ancestrylibrary.com/search/collections/3570/'],
    'md':['https://www.ancestrylibrary.com/search/collections/3552/'],
    'nc':['https://www.ancestrylibrary.com/search/collections/3005/', 
         'https://www.ancestrylibrary.com/search/collections/2234/'],
    'ga':['https://www.ancestrylibrary.com/search/collections/2234/'],
    'ri':['https://www.ancestrylibrary.com/search/collections/3571/']
}


In [12]:
# ancestry has unique urls for each state
residence_urls = {
    'nh':'_new+hampshire-usa_32',
    'nj':'_new+jersey-usa_33', 
    'ny':'_new+york-usa_35',
    'ma':'_massachusetts-usa_24',
    'ct':'_connecticut-usa_9',
    'va':'_virginia-usa_49', 
    'pa':'_pennsylvania-usa_41',
    'md':'_maryland-usa_23',
    'nc':'_north+carolina-usa_36',
    'ga':'_georgia-usa_13',
    'ri':'_rhode+island-usa_42'
}

In [13]:
fixes = {} #record name necessary name changes here

In [14]:
checked1 = [] #multiple debt entries for the same person: don't search these names again when comparing

In [15]:
checked0 = [] #multiple debt entries for the same person: don't search these names again

In [16]:
rerun_rows = [] #ancestry crashed trying to find these names

In [18]:
# remove 'cs' (congress) and 'f' (foreign officers); these are not state, but specific regiments / types of officers
agg_debt_copy = agg_debt[(agg_debt['state'] != 'cs') & (agg_debt['state'] != 'f') & (agg_debt['state'] != 'de')]

# split dataframe based on state; makes searching faster
agg_debt_sp = agg_debt_copy.groupby('state')
agg_debts_st = [agg_debt_sp.get_group(x) for x in agg_debt_sp.groups]


for x in agg_debt_sp.groups:
    print(x)
    
# add state to 'fixes' list 
for st in agg_debt_sp.groups:
    fixes[st] = {}

ct
ga
ma
md
nc
nh
nj
ny
pa
ri
va


In [19]:
netid_xpath = '/html/body/div[1]/div[2]/section/div[1]/div/form/fieldset/div[1]/input'
password_xpath = '/html/body/div[1]/div[2]/section/div[1]/div/form/fieldset/div[2]/input'
login_btn0_xpath = '/html/body/main/div/div/div/a'
login_btn1_xpath = '/html/body/div[1]/div[2]/section/div[1]/div/form/fieldset/div[3]/button'

# ask for password and username 
username = input('username: ')
password = getpass.getpass(prompt='password: ')
driver_objs = {}
# create a new driver object for each state
for st in agg_debt_sp.groups:
    driver_objs[st] = [webdriver.Chrome(service=Service(ChromeDriverManager(version='114.0.5735.16').install()), options=options)]
# create a new wait object for each state
for st in agg_debt_sp.groups:
    webdriver_obj = driver_objs[st][0]
    driver_objs[st].append(WebDriverWait(webdriver_obj, 30))
# for each driver obj: access emory's ancestry's subscription 
for st in agg_debt_sp.groups:
    webdriver_obj = driver_objs[st][0]
    wait_obj = driver_objs[st][1]
    
    # go to emory's library 
    webdriver_obj.get('https://guides.libraries.emory.edu/ALE')
    wait_obj.until(element_to_be_clickable((By.XPATH, login_btn0_xpath))).click()
    
    # input login information and click 'login'
    netid_input = wait_obj.until(element_to_be_clickable((By.XPATH, netid_xpath)))
    netid_input.click()
    netid_input.send_keys(username)
    pass_input = wait_obj.until(element_to_be_clickable((By.XPATH, password_xpath)))
    pass_input.click()
    pass_input.send_keys(password) 
    wait_obj.until(element_to_be_clickable((By.XPATH, login_btn1_xpath))).click()
    
    webdriver_obj.get('https://www.ancestrylibrary.com/search/collections/5058/')
    
    print(webdriver_obj.current_url)
    

username: dcho52
password: ········
https://www.ancestrylibrary.com/search/collections/5058/
https://www.ancestrylibrary.com/search/collections/5058/
https://www.ancestrylibrary.com/search/collections/5058/
https://www.ancestrylibrary.com/search/collections/5058/
https://www.ancestrylibrary.com/search/collections/5058/
https://ancestrylibrary.proquest.com/aleweb/ale/do/login
https://www.ancestrylibrary.com/search/collections/5058/
https://ancestrylibrary.proquest.com/aleweb/ale/do/login
https://ancestrylibrary.proquest.com/aleweb/ale/do/login
https://www.ancestrylibrary.com/search/collections/5058/
https://ancestrylibrary.proquest.com/aleweb/ale/do/login


In [20]:
'''
# check if all objects in the driver_objs are the same 
def all_same(items):
    first_item = items[list(items.keys())[0]][0]
    
    return all(first_item is items[key][0] for key in items)

all_same(driver_objs)
'''

'\n# check if all objects in the driver_objs are the same \ndef all_same(items):\n    first_item = items[list(items.keys())[0]][0]\n    \n    return all(first_item is items[key][0] for key in items)\n\nall_same(driver_objs)\n'

In [21]:
'''
swifter.set_defaults(
    allow_dask_on_strings=True,
    force_parallel=True
)
'''

'\nswifter.set_defaults(\n    allow_dask_on_strings=True,\n    force_parallel=True\n)\n'

In [22]:
def ancestry_cleaning(agg_debt_st, state):
    # retrieve selenium chromedrivers associated with that state
    st_driver = driver_objs[state][0]
    wait_driver = driver_objs[state][1]
    # run ancestry search on agg debt file
    # agg_debt_st.swifter.apply(lambda row0: compare_strings(agg_debt_st, row0['to whom due | first name'], row0['to whom due | last name'], state, row0), axis=1) # using apply
    agg_debt_clean = compare_strings_vect(agg_debt_st['to whom due | first name'].astype(str), agg_debt_st['to whom due | last name'].astype(str), state, st_driver, wait_driver) # using vectorization
    return agg_debt_st

In [23]:
# loop through the state agg_debt one more time; compare row0 (original row) with all the other rows (row1)
def compare_strings(fn0, ln0, state, st_driver, wait_driver):
    # make sure we haven't checked this name before (handles people who share the same fn & ln & live in same state) 
    # name0 = row0['to whom due | first name'] + ' ' + row0['to whom due | last name'] # uncomment when using apply
    agg_debt_st = agg_debt_sp.get_group(state)
    
    if (fn0, ln0, state) not in checked0:
        # compare both strings 
        # agg_debt_st.swifter.apply(lambda row1: fuzzy_comparison(fn0, ln0, row1['to whom due | first name'], row1['to whom due | last name'], state, row0, row1), axis=1) # using apply
        fuzzy_comparison_vect(fn0, ln0, agg_debt_st['to whom due | first name'].astype(str), agg_debt_st['to whom due | last name'].astype(str), state, st_driver, wait_driver) # using vectorization
        checked0.append((fn0, ln0, state))

In [24]:
# compare two strings using fuzzy string matching 
def fuzzy_comparison(fn0, ln0, fn1, ln1, state, st_driver, wait_driver):
    if (fn1, ln1, state) not in checked1:
        
        name0 = fn0 + ' ' + ln0
        name1 = fn1 + ' ' + ln1

        # use phonetic similarity (compares similar sounding names)
        meta0 = metaphone(name0.lower()) 
        meta1 = metaphone(name1.lower())
        phonetic_score = fuzz.ratio(meta0, meta1)

        # use fuzzy string similarity (compares similar spellings between names)
        fuzz_score = fuzz.ratio(name0, name1) 

        # check if phonetic score and fuzzy string score both meet threshold, both names are not the same  
        if phonetic_score > 90 and fuzz_score > 90 and name0 != name1:
            search_ancestry(fn0, ln0, fn1, ln1, name0, name1, state, st_driver, wait_driver) 
            checked1.append((fn1, ln1, state)) # record that we have checked this name

In [25]:
# look up both names in ancestry's database
def search_ancestry(fn0, ln0, fn1, ln1, name0, name1, state, driver, wait):
    # loop through state urls 
    for url in records[state]:        
        try:
            # search person-0
            url0 = url + '?name=' + fn0 + '_' + ln0 + '&name_x=ps&residence=1780' + residence_urls[state] + '&residence_x=10-0-0_1-0'
            driver.get(url0) 
                        
            # results were found for person0
            try:
                # use xpath to find result text
                # result0 = wait.until(presence_of_element_located((By.XPATH, '/html/body/div[3]/div/div/div/section[1]/div[1]/table/tbody/tr[2]/td[2]/span'))).text
                # use class_name to find result text
                result0 = wait.until(presence_of_element_located((By.CLASS_NAME, 'srchHit'))).text
            # no results were found; keep entries separate  
            except:
                result0 = ''
            
            # search person-1
            url1 = url + '?name=' + fn1 + '_' + ln1 + '&name_x=ps&residence=1780' + residence_urls[state] + '&residence_x=10-0-0_1-0'
            driver.get(url1)
                        
            # results were found for person1
            try: 
                # use xpath to find result text
                # result1 = wait.until(presence_of_element_located((By.XPATH, '/html/body/div[3]/div/div/div/section[1]/div[1]/table/tbody/tr[2]/td[2]/span'))).text
                # use class_name to find result text
                result1 = wait.until(presence_of_element_located((By.CLASS_NAME, 'srchHit'))).text
            # no results were found; keep entries separate
            except:
                result1 = ''
                
            '''
            compare results:
            if both results are empty, do not add to fixes dict 
            if both results are different, do not add to fixes dict
            if both results are the same, add to fixes dict
                find correct name
                if name0 = result0 and result1 : {name1 : name0}
                if name1 = result1 and result0 : {name0 : name0} 
            '''
            
            if result0 == result1 and result0 != '' and result1 != '':
                if name0 == result0 and name0 == result1: # name0 must be the correct version of the name 
                    fixes[state][(fn1, ln1, name1)] = (fn0, ln0, name0) # convert name1 to name0  
                    # record change
                    '''
                    add_changes(row1['to whom due | title'], row1['to whom due | title'], fn1, ln1, 
                       fn0, ln0, 6, row1['org_file'], row1['org_index'])
                    '''

                elif name1 == result0 and name1 == result1: # name1 must be the correct version of the name 
                    fixes[state][(fn0, ln0, name0)] = (fn1, ln1, name1) # convert name0 to name1
                    # record change
                    '''
                    add_changes(row0['to whom due | title'], row0['to whom due | title'], fn0, ln0, 
                       fn1, ln1, 6, row0['org_file'], row0['org_index'])
                    '''
            
            print('---------------------------+')
            print('Summary')
            print('driver=')
            print(driver)
            print('name0=' + str(name0))
            print('name1=' + str(name1))
            print('fn0=' + str(fn0))
            print('ln0=' + str(ln0))
            print('fn1=' + str(fn1))
            print('ln1=' + str(ln1))
            print('url-0=' + str(url0))
            print('url-1=' + str(url1))
            print('result0=' + str(result0))
            print('result1=' + str(result1))
            print('state=' + str(state))
            print('fixes length=' + str(len(fixes[state])))
            print('rerun rows length=' + str(len(rerun_rows)))
            print('---------------------------+')
        
        # there was error trying to access ancestry's records
        except Exception as e:
            print('---------------------------+')
            print('Error')
            print(e)
            print('name0=' + str(name0))
            print('name1=' + str(name1))
            print('---------------------------+')
            rerun_rows.append([fn0, ln0, fn1, ln1, name0, name1, state]) 

In [ ]:
# record how long it takes to run ancestry search; useful information to see effectiveness of different methods 
start = time.time()

# vectorize our functions 
compare_strings_vect = np.vectorize(compare_strings)
fuzzy_comparison_vect = np.vectorize(fuzzy_comparison)

# initialize a parallelization job; the idea is to have one core work on one state's agg debt file

ancestry_calls = [delayed(ancestry_cleaning)(agg_debt_sp.get_group(st), st) for st in agg_debt_sp.groups]
results = Parallel(n_jobs=-1, backend="threading")(ancestry_calls) 

# split nj's agg_debt file to test parallelization
# agg_debt_nj = agg_debt_sp.get_group('nj')
# agg_debt_nj_sp = np.split(agg_debt_nj, 7)

# initialize parallelization (nj)
# ancestry_calls = [delayed(ancestry_cleaning)(df, st) for df in agg_debt_nj_sp.groups]
# results = Parallel(n_jobs=-1, backend="threading")(ancestry_calls) 

# try without parallization - try out on [nj] only
# agg_debt_nj = ancestry_cleaning(agg_debt_sp.get_group('nj'), 'nj')

end = time.time()
print(end - start)

---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="81b32a47631da187e19df4b334b414d2")>
name0=Isaac Peirce
name1=Isaac Pierce
fn0=Isaac
ln0=Peirce
fn1=Isaac
ln1=Pierce
url-0=https://www.ancestrylibrary.com/search/collections/5058/?name=Isaac_Peirce&name_x=ps&residence=1780_massachusetts-usa_24&residence_x=10-0-0_1-0
url-1=https://www.ancestrylibrary.com/search/collections/5058/?name=Isaac_Pierce&name_x=ps&residence=1780_massachusetts-usa_24&residence_x=10-0-0_1-0
result0=Isaac Peirce
result1=Isaac Pierce
state=ma
fixes length=0
rerun rows length=0
---------------------------+
---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="3bf463614ac868422d3c7751c58f6736")>
name0=Furman & Hunt nan
name1=Forman & Hunt nan
fn0=Furman & Hunt
ln0=nan
fn1=Forman & Hunt
ln1=nan
url-0=https://www.ancestrylibrary.com/search/collections/2234/?name=Furman & Hunt_nan&name_x=ps&residence=1780_new+jersey-usa_33&

---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="bee9d532f27dbe0d1fb5e2eb2098e44f")>
name0=James Gallaway
name1=James Galloway
fn0=James
ln0=Gallaway
fn1=James
ln1=Galloway
url-0=https://www.ancestrylibrary.com/search/collections/5058/?name=James_Gallaway&name_x=ps&residence=1780_new+york-usa_35&residence_x=10-0-0_1-0
url-1=https://www.ancestrylibrary.com/search/collections/5058/?name=James_Galloway&name_x=ps&residence=1780_new+york-usa_35&residence_x=10-0-0_1-0
result0=
result1=
state=ny
fixes length=0
rerun rows length=0
---------------------------+
---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="087dd51c8ba58bf891937bd60977dbd6")>
name0=Gad Alderman
name1=Gad Aldeman
fn0=Gad
ln0=Alderman
fn1=Gad
ln1=Aldeman
url-0=https://www.ancestrylibrary.com/search/collections/5058/?name=Gad_Alderman&name_x=ps&residence=1780_connecticut-usa_9&residence_x=10-0-0_1-0
url-1=https://www.ancestry

---------------------------+---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="81b32a47631da187e19df4b334b414d2")>
name0=Israel Beals
name1=Israel Beal
fn0=Israel
ln0=Beals
fn1=Israel
ln1=Beal
url-0=https://www.ancestrylibrary.com/search/collections/5058/?name=Israel_Beals&name_x=ps&residence=1780_massachusetts-usa_24&residence_x=10-0-0_1-0
url-1=https://www.ancestrylibrary.com/search/collections/5058/?name=Israel_Beal&name_x=ps&residence=1780_massachusetts-usa_24&residence_x=10-0-0_1-0
result0=Israel Beal
result1=Israel Beal
state=ma
fixes length=3
rerun rows length=0
---------------------------+

Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="ee65bf2d298d78ad5af7014e0944e53f")>
name0=John Armsbree
name1=John Armsbre
fn0=John
ln0=Armsbree
fn1=John
ln1=Armsbre
url-0=https://www.ancestrylibrary.com/search/collections/3571/?name=John_Armsbree&name_x=ps&residence=1780_rhode+island-usa_42&residence_x=10-0-0_1-0
ur

---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="087dd51c8ba58bf891937bd60977dbd6")>
name0=David Atkins
name1=Divid Atkins
fn0=David
ln0=Atkins
fn1=Divid
ln1=Atkins
url-0=https://www.ancestrylibrary.com/search/collections/5058/?name=David_Atkins&name_x=ps&residence=1780_connecticut-usa_9&residence_x=10-0-0_1-0
url-1=https://www.ancestrylibrary.com/search/collections/5058/?name=Divid_Atkins&name_x=ps&residence=1780_connecticut-usa_9&residence_x=10-0-0_1-0
result0=David Atkins 
result1=David Atkins 
state=ct
fixes length=2
rerun rows length=0
---------------------------+
---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="087dd51c8ba58bf891937bd60977dbd6")>
name0=Divid Atkins
name1=David Atkins
fn0=Divid
ln0=Atkins
fn1=David
ln1=Atkins
url-0=https://www.ancestrylibrary.com/search/collections/5058/?name=Divid_Atkins&name_x=ps&residence=1780_connecticut-usa_9&residence_x=10-0-0_1-0
url-1=

---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="99795536cd518afba2bb9c38c87011a9")>
name0=Jacob Adamson
name1=Jacob Adams
fn0=Jacob
ln0=Adamson
fn1=Jacob
ln1=Adams
url-0=https://www.ancestrylibrary.com/search/collections/3552/?name=Jacob_Adamson&name_x=ps&residence=1780_maryland-usa_23&residence_x=10-0-0_1-0
url-1=https://www.ancestrylibrary.com/search/collections/3552/?name=Jacob_Adams&name_x=ps&residence=1780_maryland-usa_23&residence_x=10-0-0_1-0
result0=
result1=Jacob Adam
state=md
fixes length=0
rerun rows length=0
---------------------------+
---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="99795536cd518afba2bb9c38c87011a9")>
name0=James Alien
name1=James Allen
fn0=James
ln0=Alien
fn1=James
ln1=Allen
url-0=https://www.ancestrylibrary.com/search/collections/3552/?name=James_Alien&name_x=ps&residence=1780_maryland-usa_23&residence_x=10-0-0_1-0
url-1=https://www.ancestrylibrary

---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="d33166fb4347cbadccea74aa91a75ac6")>
name0=Daniel Peirce
name1=Daniel Pierce
fn0=Daniel
ln0=Peirce
fn1=Daniel
ln1=Pierce
url-0=https://www.ancestrylibrary.com/search/collections/5058/?name=Daniel_Peirce&name_x=ps&residence=1780_new+hampshire-usa_32&residence_x=10-0-0_1-0
url-1=https://www.ancestrylibrary.com/search/collections/5058/?name=Daniel_Pierce&name_x=ps&residence=1780_new+hampshire-usa_32&residence_x=10-0-0_1-0
result0=
result1=
state=nh
fixes length=0
rerun rows length=0
---------------------------+
---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="81b32a47631da187e19df4b334b414d2")>
name0=Ebenezer Wycth
name1=Ebenezer Wyeth
fn0=Ebenezer
ln0=Wycth
fn1=Ebenezer
ln1=Wyeth
url-0=https://www.ancestrylibrary.com/search/collections/5058/?name=Ebenezer_Wycth&name_x=ps&residence=1780_massachusetts-usa_24&residence_x=10-0-0_1-0
url-1=h

---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="8feda1317f7f27a817032ccfa772e96b")>
name0=George Adams
name1=George Adam
fn0=George
ln0=Adams
fn1=George
ln1=Adam
url-0=https://www.ancestrylibrary.com/search/collections/2234/?name=George_Adams&name_x=ps&residence=1780_pennsylvania-usa_41&residence_x=10-0-0_1-0
url-1=https://www.ancestrylibrary.com/search/collections/2234/?name=George_Adam&name_x=ps&residence=1780_pennsylvania-usa_41&residence_x=10-0-0_1-0
result0=
result1=
state=pa
fixes length=0
rerun rows length=0
---------------------------+
---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="81b32a47631da187e19df4b334b414d2")>
name0=William Gorden
name1=William Gordon
fn0=William
ln0=Gorden
fn1=William
ln1=Gordon
url-0=https://www.ancestrylibrary.com/search/collections/5058/?name=William_Gorden&name_x=ps&residence=1780_massachusetts-usa_24&residence_x=10-0-0_1-0
url-1=https://www.

---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="81b32a47631da187e19df4b334b414d2")>
name0=John White
name1=John Whittey
fn0=John
ln0=White
fn1=John
ln1=Whittey
url-0=https://www.ancestrylibrary.com/search/collections/5058/?name=John_White&name_x=ps&residence=1780_massachusetts-usa_24&residence_x=10-0-0_1-0
url-1=https://www.ancestrylibrary.com/search/collections/5058/?name=John_Whittey&name_x=ps&residence=1780_massachusetts-usa_24&residence_x=10-0-0_1-0
result0=John White
result1=
state=ma
fixes length=8
rerun rows length=0
---------------------------+
---------------------------+
Summary
driver=
<selenium.webdriver.chrome.webdriver.WebDriver (session="f137a470ae57de5b5c84851e7094cc7f")>
name0=Brossard Celeren
name1=Brossard Celerin
fn0=Brossard
ln0=Celeren
fn1=Brossard
ln1=Celerin
url-0=https://www.ancestrylibrary.com/search/collections/2234/?name=Brossard_Celeren&name_x=ps&residence=1780_georgia-usa_13&residence_x=10-0-0_1-0
url-1

In [ ]:
# save fixes
fixes_df = pd.DataFrame(fixes)
fixes_df.to_csv('fixes.csv')

In [ ]:
# save rerun rows
with open('data/rerun.csv', 'w', newline='') as rerun_csv:
    writer = csv.writer(rerun_csv) 
    writer.writerows(rerun_rows)

In [ ]:
# save new agg_debt 
agg_debt.to_csv('data/agg_debt_clean_david.csv')

In [ ]:
# save name changes 
name_changes.to_csv('data/name_changes_david.csv')

In [ ]:
# test 
# search_ancestry('John', 'Smith', '', '', 'ny')

In [ ]:
# regroup rows with the same indexes : these were individuals who shared debt entries 
column_map = {col: "first" for col in agg_debt.columns}
column_map['to whom due | first name'] = lambda x: x.tolist() if len(x) > 1 else x
column_map['to whom due | last name'] = lambda x: x.tolist() if len(x) > 1 else x

agg_debt = (agg_debt.groupby(['index'])
      .agg(column_map).reset_index(drop=True))

agg_debt

### Old Ancestry Cleaning

In [ ]:
def access_ancestry(fn0, ln0, c_fn, c_ln, state, row0, c_row):
    name0 = fn0 + ' ' + ln0 # static
    c_name = c_fn + ' ' + c_ln # changing
    
    driver.get('https://www.ancestrylibrary.com/search/collections/5058/?name=' + fn0 + '_' + ln0 + '&residence=' + ancestry_state_urls[state] + '&residence_x=10-0-0_1-0')
    print(driver.current_url)
    
    try:
        try:
            check_exists = driver.find_element(By.XPATH, '/html/body/div[3]/div/div/div/section[1]/div[1]/div/div')
            result1 = name0
            result2 = c_name
        except NoSuchElementException:  
            result = wait.until(presence_of_element_located((By.XPATH, '/html/body/div[3]/div/div/div/section[1]/div[1]/table/tbody/tr[2]/td[2]/span'))).text
            result_name = HumanName(result)

            if result_name.middle != '':
                result1 = result_name.first + ' ' + result_name.middle + ' ' + result_name.last
            else:
                result1 = result_name.first + ' ' + result_name.last
        
        print('index: ' + str(row0['index1']))
        print('first ancestry result: ' + result1)

        driver.get('https://www.ancestrylibrary.com/search/collections/5058/?name=' + c_fn + '_' + c_ln + '&residence=' + ancestry_state_urls[state] + '&residence_x=_1-0')
        print(driver.current_url)

        try:
            check_exists = driver.find_element(By.XPATH, '/html/body/div[3]/div/div/div/section[1]/div[1]/div/div')
            result1 = name0
            result2 = c_name
        except NoSuchElementException:
            result = wait.until(presence_of_element_located((By.XPATH, '/html/body/div[3]/div/div/div/section[1]/div[1]/table/tbody/tr[2]/td[2]/span'))).text
            result_name = HumanName(result)

            if result_name.middle != '':
                result2 = result_name.first + ' ' + result_name.middle + ' ' + result_name.last
            else:
                result2 = result_name.first + ' ' + result_name.last

        print('second ancestry result: ' + result2) 

        if result1 == name0 and result2 == name0: # name0 is the correct spelling of the name
            fixes.append([state, {c_name:name0}])
            
            # record changes
            add_changes(c_row['to whom due | title'], c_row['to whom due | title'], c_row['to whom due | first name'],
                        c_row['to whom due | last name'], fn0, ln0, 6, c_row['org_file'], c_row['org_index'])
        elif result1 == c_name and result2 == c_name: # c_name is the correct spelling of the name
            fixes.append([state, {name0:c_name}])
            
            # record changes
            add_changes(row0['to whom due | title'], row0['to whom due | title'], row0['to whom due | first name'],
                        row0['to whom due | last name'], c_fn, c_ln, 6, row0['org_file'], row0['org_index'])
    except:
        rerun_rows.append([row0, c_row])

def only_f(row0, row):
    try:
        if row['to whom due | first name'][0] == row0['to whom due | first name'][0] and row['to whom due | last name'][0] == row0['to whom due | last name'][0] and row['state'] == row0['state']:
            return row
    except:
        return 

def fuzzy_similarity(c_row, row0):
    name = row0['to whom due | first name'] + ' ' + row0['to whom due | last name']
    cname = c_row['to whom due | first name'] + ' ' + c_row['to whom due | last name']
    
    # check fuzzy string ratio and metaphone ratio
    code1 = metaphone(name)
    code2 = metaphone(cname)
    ratio = fuzz.ratio(name, cname)
    score = fuzz.ratio(code1, code2)

    # only search ancestry when the two names have a ratio greater than 90, the names don't equal each other, 
    # and we haven't checled current name already
    if score > 90 and ratio > 90 and name != cname and (cname not in c_checked):
        print('name: ' + name)
        print('comparing to name: ' + cname)
        
        correct_name = access_ancestry(row0['to whom due | first name'], row0['to whom due | last name'],
                                       c_row['to whom due | first name'], c_row['to whom due | last name'], row0['state'], row0, c_row)
            
        print('--------------------------------------------------')
        c_checked.append(cname)
    
def determine_similarities(row0):
    current_name = row0['to whom due | first name'] + ' ' + row0['to whom due | last name']
    
    # only search ancestry when ancestry has records and if we have not checked name already
    if (row0['state'] in ancestry_state_urls) and ([row0['state'], current_name] not in checked0):
        
        # shorten table to only include names that share first letter of first name and last name and come from the same state
        short_table = agg_debt.apply(lambda row: only_f(row0, row), axis=1).dropna()

        if len(short_table) > 0:
            c_checked.clear()
            short_table.apply(lambda row: fuzzy_similarity(row, row0))
            
        checked0.append([row0['state'], current_name])
                        
    if len(fixes) % 5 == 0 and len(fixes) > 0:
        print(fixes[len(fixes) - 1]) 
    
agg_debt['to whom due | first name'] = agg_debt['to whom due | first name'].astype(str)
agg_debt['to whom due | last name'] = agg_debt['to whom due | last name'].astype(str)
agg_debt.sort_values('to whom due | last name', inplace=True)
agg_debt.reset_index(inplace=True)
agg_debt['index1'] = agg_debt.index
agg_debt.apply(lambda row: determine_similarities(agg_debt, row), axis=1)

In [ ]:
# save agg_debt as csv file: 'out.csv'
agg_debt.to_csv('data/agg_debt_clean.csv')

In [ ]:
with open('data/out.csv', 'r') as read_obj:

    csv_reader = csv.reader(read_obj)
  
    # convert string to list
    entries = list(csv_reader)
    
    # remove empty lists
    entries = [entry for entry in entries if entry != []]
  
    print(entries)

In [ ]:
# reorganize entries and group by state
entries_dict = {}
for entry in entries:
    if entry[0] not in entries_dict:
        entries_dict[entry[0]] = [entry]
    else:
        entries_dict[entry[0]] += [entry]

print(entries_dict)

In [ ]:
# implement changes to agg_debt
def implement_name_changes(row):  
    if str(row['state']) not in entries_dict:
        return row 
    
    # only select part of the list that belongs to one person 
    entries_red = entries_dict[row['state']]
    
    # loop through list
    # check if name matches 
    full_name = str(row['to whom due | first name']) + ' ' + str(row['to whom due | last name'])
    
    for entry in entries_red:
        name_dict = ast.literal_eval(entry[1])
        
        if full_name in name_dict:
            new_name = name_dict[full_name]
            new_name_l = new_name.split()
            new_fn = ''
            new_ln = ''
            
            # account for middle initials and middle names
            if len(new_name_l) >= 3:
                name = HumanName(new_name)
                
                if len(name.middle) == 1: # middle initial
                    new_fn = name.first + ' ' + name.middle 
                    new_ln = name.last
                elif len(name.middle) > 1: # middle name
                    new_fn = name.first
                    new_ln = name.middle + ' ' + name.last
                else: # no middle name 
                    new_fn = name.first
                    new_ln = name.last
                    
            # if there is only a first name and a last name 
            else:
                new_fn = new_name_l[0]
                new_ln = new_name_l[1] 
            
            # record changes
            add_changes(row['to whom due | title'], row['to whom due | title'], row['to whom due | first name'], row['to whom due | last name'], 
                   new_fn, new_ln, 6, row['org_file'], row['org_index'])
            
            # remove unncessary spaces at the end of the string 
            new_fn.strip()
            new_ln.strip()
            
            row['to whom due | first name'] = new_fn 
            row['to whom due | last name'] = new_ln
            
            print('old name=' + full_name)
            print('new first name=' + new_fn)
            print('new last name=' + new_ln)
            print('name_changes status=' + str(len(name_changes)))
            print('------------------')
            
    return row

agg_debt = agg_debt.apply(lambda row: implement_name_changes(row), axis=1)

In [ ]:
agg_debt.head()